# Objects in the Greater Melbourne Region

The VicRoad Data Exchange Platform provides Bluetooth data for various links and sites across the entire state of Victoria. However, the distribution of this data is uneven. Most of the regions outside the Greater Melbourne Region offer sparse data, to such an extent that it's hard to create an integrated road network in some areas. Consequently, our research is primarily focused on the Greater Melbourne Region.

This area has a dense concentration of links, allowing for the construction of a complex road network. In this particular dataset, our task is to filter and extract the links which have both their origin and destination points located within the Greater Melbourne Region.

In [62]:
import pandas as pd
import numpy as np
import json
import geopandas as gpd
from shapely.geometry import Point, LineString
import folium

## 1 LGA in the Greater Melbourne Region

The 31 subcategories of the Greater Melbourne Region can be found in [Wikipedia - Category: Greater Melbourne (region)](https://en.wikipedia.org/wiki/Category:Greater_Melbourne_(region)).

In [63]:
lgas_gdf = gpd.read_file('./dist/lgas_wgs84.geojson')

GREATE_MELBOURNE_REGIONS = ["Banyule", "Bayside", "Boroondara", "Brimbank", "Casey", "Darebin", "Frankston",
                            "Glen Eira", "Greater Dandenong", "Hobsons Bay", "Hume", "Kingston", "Knox", "Manningham",
                            "Maribyrnong", "Maroondah", "Melbourne", "Melton", "Merri-bek", "Monash", "Moonee Valley",
                            "Port Phillip", "Stonnington", "Whitehorse", "Whittlesea", "Wyndham", "Yarra", "Cardinia",
                            "Mornington Peninsula", "Nillumbik", "Yarra Ranges"]
# convert the list to lowercase
GREATE_MELBOURNE_REGIONS_lower = [region.lower() for region in GREATE_MELBOURNE_REGIONS]

# convert the DataFrame column to lowercase for the comparison
melbourne_lgas_gdf = lgas_gdf[lgas_gdf["ABB_NAME"].str.lower().isin(GREATE_MELBOURNE_REGIONS_lower)]
assert len(melbourne_lgas_gdf) == len(GREATE_MELBOURNE_REGIONS)
melbourne_lgas_gdf

LGA_PID                    LGA_NAME              ABB_NAME   
3   lga5591321694d6                Banyule City               Banyule  \
8   lga53f7b61b0ed6                Bayside City               Bayside   
10  lga0930e8ebad68             Boroondara City            Boroondara   
11  lgaf76bb579e827               Brimbank City              Brimbank   
14  lgac69cfd288672              Cardinia Shire              Cardinia   
15  lga891e1f62b45e                  Casey City                 Casey   
19  lga5bfafb32b8d5                Darebin City               Darebin   
22  lgadd7fe82edc77              Frankston City             Frankston   
28  lga9bd137c30d17              Glen Eira City             Glen Eira   
32  lgab65bc8ec7820      Greater Dandenong City     Greater Dandenong   
37  lga224186279c28            Hobsons Bay City           Hobsons Bay   
39  lga3476c1d9fd7f                   Hume City                  Hume   
41  lga691f580f3258               Kingston City              Kingston   
42  lgaacfaedf6a58f                   Knox City                  Knox   
47  lgab3be0b9eb31a             Manningham City            Manningham   
49  lga2513fbdd7033            Maribyrnong City           Maribyrnong   
50  lgafa7d75c94e0c              Maroondah City             Maroondah   
51  lgadd6ba71d5cd0              Melbourne City             Melbourne   
52  lga42b2fd54c1e9                 Melton City                Melton   
53  lgaJ2LPN2y4pll0              Merri-Bek City             Merri-Bek   
57  lga15c9c80d4be7                 Monash City                Monash   
58  lga638d2708b9ab          Moonee Valley City         Moonee Valley   
60  lga69684c885dd2  Mornington Peninsula Shire  Mornington Peninsula   
69  lga977c9605ab7d             Nillumbik Shire             Nillumbik   
71  lgad68479123642           Port Phillip City          Port Phillip   
76  lgae1dcbacb8510            Stonnington City           Stonnington   
85  lga0450031d71ce             Whitehorse City            Whitehorse   
86  lgaa0f71a56be3f             Whittlesea City            Whittlesea   
88  lga53026dafea91                Wyndham City               Wyndham   
89  lga4449559268d6                  Yarra City                 Yarra   
90  lgadbd419ff24e3          Yarra Ranges Shire          Yarra Ranges   

                                             geometry  
3   POLYGON ((145.02805 -37.76410, 145.02789 -37.7...  
8   POLYGON ((145.00755 -37.95811, 145.00725 -37.9...  
10  POLYGON ((145.10207 -37.81533, 145.10166 -37.8...  
11  POLYGON ((144.86945 -37.72217, 144.86384 -37.7...  
14  POLYGON ((145.75500 -38.12589, 145.75495 -38.1...  
15  POLYGON ((145.31027 -38.22042, 145.31058 -38.2...  
19  POLYGON ((145.02838 -37.76420, 145.02848 -37.7...  
22  POLYGON ((145.22457 -38.15422, 145.22437 -38.1...  
28  POLYGON ((145.02354 -37.91480, 145.02356 -37.9...  
32  POLYGON ((145.22855 -37.99371, 145.22855 -37.9...  
37  POLYGON ((144.91347 -37.86680, 144.91344 -37.8...  
39  POLYGON ((144.95856 -37.62957, 144.95848 -37.6...  
41  POLYGON ((145.10913 -38.04420, 145.10888 -38.0...  
42  POLYGON ((145.30917 -37.88954, 145.30943 -37.8...  
47  POLYGON ((145.09396 -37.77930, 145.09357 -37.7...  
49  POLYGON ((144.90970 -37.79403, 144.90984 -37.7...  
50  POLYGON ((145.31756 -37.82348, 145.31873 -37.8...  
51  POLYGON ((144.96170 -37.82811, 144.96166 -37.8...  
52  POLYGON ((144.51513 -37.69841, 144.51479 -37.6...  
53  POLYGON ((144.93680 -37.76022, 144.93653 -37.7...  
57  POLYGON ((145.20387 -37.91483, 145.20385 -37.9...  
58  POLYGON ((144.86645 -37.77212, 144.86630 -37.7...  
60  POLYGON ((145.21242 -38.37899, 145.21213 -38.3...  
69  POLYGON ((145.11684 -37.68791, 145.11435 -37.6...  
71  POLYGON ((144.96115 -37.85456, 144.96092 -37.8...  
76  POLYGON ((145.04029 -37.84468, 145.04028 -37.8...  
85  POLYGON ((145.21318 -37.81131, 145.21319 -37.8...  
86  POLYGON ((145.10498 -37.64727, 145.10518 -37.6...  
88  POLYGON ((144.68301 -37.97230, 144.68284 -37.9.

## 2 Links in the Greater Melbourne Region

In [64]:
links_gdf = gpd.read_file('./dist/links_wgs84.geojson')
links_gdf

id                                               name  length   
0        3           Bulleen Rd, Eastern Fwy to Manningham Rd    2000  \
1        5              Greensborough Hwy, M80 to Grimshaw St    1100   
2        6              Greensborough Hwy, Grimshaw St to M80    1100   
3        7      Greensborough Hwy, Grimshaw St to Watsonia Rd    1400   
4        8      Greensborough Hwy, Watsonia Rd to Grimshaw St    1400   
...    ...                                                ...     ...   
4733  5512  DEM Sunbury Rd, Oaklands Rd to Melbourne-Lance...    9336   
4734  5513         DEM Oaklands Rd, Somerton Rd to Sunbury Rd    1656   
4735  5514          Sunbury & Oaklands to Oaklands & Somerton    1649   
4736  5515  Western Port Hwy, Ballarto Rd to Cranbourne - ...    1340   
4737  5516  Western Port Hwy, Cranbourne - Frankston Rd to...    1340   

      min_number_of_lanes  is_freeway direction  origin.id  destination.id   
0                       1       False        NB       2827             686  \
1                       1       False        SB       3357            4187   
2                       1       False        NB       4187            3357   
3                       1       False        SB       4187            3341   
4                       1       False        NB       3341            4187   
...                   ...         ...       ...        ...             ...   
4733                    1       False       NWB      31809           31802   
4734                    1       False        SB      31801           31809   
4735                    1       False        NB      31809           31801   
4736                    1       False        SB      32015           32014   
4737                    1       False        NB      32014           32015   

                                               geometry  
0     LINESTRING (145.07840 -37.77962, 145.07848 -37...  
1     LINESTRING (145.09357 -37.69418, 145.09332 -37...  
2     LINESTRING (145.08958 -37.70316, 145.08963 -37...  
3     LINESTRING (145.09003 -37.70324, 145.08981 -37...  
4     LINESTRING (145.08263 -37.71442, 145.08276 -37...  
...                                                 ...  
4733  LINESTRING (144.83385 -37.64433, 144.83354 -37...  
4734  LINESTRING (144.83660 -37.62963, 144.83595 -37...  
4735  LINESTRING (144.83362 -37.64410, 144.83382 -37...  
4736  LINESTRING (145.23099 -38.12197, 145.23079 -38...  
4737  LINESTRING (145.22815 -38.13380, 145.22821 -38...  

[4738 rows x 9 columns]

In [65]:
origin_gdf = links_gdf['geometry'].apply(lambda line: Point(line.coords[0]))
destination_gdf = links_gdf['geometry'].apply(lambda line: Point(line.coords[-1]))

# Check if the origin and destination points of each line are within any polygon
origins_within = gpd.sjoin(gpd.GeoDataFrame(geometry=origin_gdf), melbourne_lgas_gdf, predicate='within')
destinations_within = gpd.sjoin(gpd.GeoDataFrame(geometry=destination_gdf), melbourne_lgas_gdf, predicate='within')
links_in_melbourne_lgas_indexes = origins_within.index.intersection(destinations_within.index)

# Use the mask to filter the lines GeoDataFrame
links_gdf_in_melbourne_lgas = links_gdf.loc[links_in_melbourne_lgas_indexes]
links_gdf_in_melbourne_lgas

id                                               name  length   
0        3           Bulleen Rd, Eastern Fwy to Manningham Rd    2000  \
42     109               Thompsons Rd, Bulleen Rd to Barak St     720   
69     166               Toorak Rd, Tooronga Rd to Monash Fwy     400   
70     167                 Toorak Rd, Tooronga Rd to Burke Rd     800   
71     168                 Toorak Rd, Burke Rd to Tooronga Rd     800   
...    ...                                                ...     ...   
4320  5097  DEM Western Fwy IB, at Ballarat Rd interchange...    1191   
4425  5202  DEM Hopkins Road/Western Freeway Ramp to DOHER...    8100   
4494  5272  DEM WESTERN FWY CHRISTIES CAROLINE SPRING to W...    1285   
4712  5491  WESTERN FREEWAY WB RAMPS/FERRIS RD to Melton H...    1468   
4713  5492  Melton Hwy & Federation Dr to WESTERN FREEWAY ...    1468   

      min_number_of_lanes  is_freeway direction  origin.id  destination.id   
0                       1       False        NB       2827             686  \
42                      1       False        EB       2827             688   
69                      1       False        WB       4273            2843   
70                      1       False        EB       4273            4043   
71                      1       False        WB       4043            4273   
...                   ...         ...       ...        ...             ...   
4320                    1       False        WB      31724            2658   
4425                    1       False        SB      31834           31863   
4494                    1       False        WB       2658           31724   
4712                    1       False        NB      31548           31799   
4713                    1       False        SB      31799           31548   

                                               geometry  
0     LINESTRING (145.07840 -37.77962, 145.07848 -37...  
42    LINESTRING (145.07860 -37.77945, 145.07980 -37...  
69    LINESTRING (145.04498 -37.84562, 145.04336 -37...  
70    LINESTRING (145.04500 -37.84526, 145.04662 -37...  
71    LINESTRING (145.05339 -37.84583, 145.05232 -37...  
...                                                 ...  
4320  LINESTRING (144.72780 -37.75169, 144.73204 -37...  
4425  LINESTRING (144.70187 -37.74800, 144.70189 -37...  
4494  LINESTRING (144.73960 -37.75650, 144.73877 -37...  
4712  LINESTRING (144.60333 -37.69724, 144.60379 -37...  
4713  LINESTRING (144.60706 -37.68475, 144.60660 -37...  

[4263 rows x 9 columns]

The number of original links is 4738, and there are 4263 links after filtering.

## 3 Map of the Greater Melbourne Region

In [66]:
MELBOURNE_CITY_COORDS = [-37.8136, 144.9631]

# Create a Map instance Cartodbdark_matter
links_map = folium.Map(location=MELBOURNE_CITY_COORDS, tiles='Cartodbdark_matter', zoom_start=10.5, zoom_control=True, scrollWheelZoom=False,
                       dragging=True)

links_network = folium.GeoJson(links_gdf_in_melbourne_lgas, name='Link Network in the Greater Melbourne',
                               style_function=lambda feature: {
                                   'color': '#32CD32' if feature['properties']['is_freeway'] == False else '#ff0000',
                                   'weight': 1},
                               tooltip=folium.features.GeoJsonTooltip(fields=['name']))
links_network.add_to(links_map)

melbourne_lgas = folium.GeoJson(melbourne_lgas_gdf, name='LGA in the Greater Melbourne',
                                style_function=lambda feature: {'color': '#d3d3d3', 'weight': 0.8},
                                tooltip=folium.features.GeoJsonTooltip(fields=['LGA_NAME']))
melbourne_lgas.add_to(links_map)
links_map

## 4 Save Links and LGAs of the Greater Melbourne Region

In [67]:
gpd.GeoDataFrame(links_gdf_in_melbourne_lgas, geometry='geometry').to_file('./dist/links_melbourne_wgs84.geojson', driver='GeoJSON', index=False)

gpd.GeoDataFrame(melbourne_lgas_gdf, geometry='geometry').to_file('./dist/lgas_melbourne_wgs84.geojson', driver='GeoJSON', index=False)